In [6]:
import os
import numpy as np
import pandas as pd

from datetime import datetime
from matplotlib import pyplot as plt
from scipy.optimize import curve_fit
# axes_grid1 should be deprecated soon but this method is, seemingly, still not fully ported
from mpl_toolkits.axes_grid1.inset_locator import mark_inset
from matplotlib.lines import Line2D
from matplotlib.patches import Rectangle
import matplotlib.dates as mdates
from chill_models import *
from ground_truth_annotations import annotate_gt

plt.rcParams['figure.figsize'] = 12, 9
plt.rcParams['figure.dpi'] = 1200
# plt.rcParams['figure.dpi'] = 100

In [3]:
retained = ['temp. C', 'Humidity %', 'UV level, W/m2', 'Insolation, kW/m2', 'Fv/Fm', 'Fo', 'Fm', 'DIo/RC', 
            'fMaxDark', 'PI', 'PSIo', 'Sm', 'VI', 'VK', 'Area']
df = pd.read_csv('merged-insol-fixed.csv', sep=';', parse_dates=[0], index_col=0)[retained]
df.fillna({'Insolation, kW/m2': 0}, inplace=True)
df.rename(columns={'temp. C': 'temp'}, inplace=True)

In [4]:
def reset_september(s: pd.Series) -> pd.Series:
    return reset_chill_hours(s, datetime(2020, 9, 1))

df['chilling_hours'] = reset_september(chilling_hours(df))
df['utah'] = reset_september(utah(df))
df['pcu'] = reset_september(positive_chill_units(df))
df['low_chill'] = reset_september(low_chill(df))
df['north_carolina'] = reset_september(north_carolina(df))
# df['landsberg'] = reset_september(landsberg(df, ))

In [7]:
plt.rcParams['figure.figsize'] = 12, 9
df['chilling_hours'].plot(label='Chilling hours')
df['utah'].plot(label='Utah')
df['pcu'].plot(label='Positive Chill Units (PCU)')
df['low_chill'].plot(label='Low chill')
df['north_carolina'].plot(label='North Carolina')
plt.gca().fill_between(df.index, 750, 1100, facecolor='0.8', edgecolor='0.2', hatch='xx', alpha=0.6, label='Range of commonly used thresholds for dormancy release', zorder=0)
handles, labels = plt.gca().get_legend_handles_labels()
# handles.append(model_label)
legend_models = plt.legend(handles=handles, loc='upper left')
plt.xlim(df.index[0], df.index[-1])
plt.ylim(0, 6000)
plt.ylabel('CU, adj. hours')
gt_handles, _ = plt.gca().get_legend_handles_labels()
plt.legend(handles=gt_handles[-2:], loc='upper right', title='Destructive tests:')
plt.gca().add_artist(legend_models)
annotate_gt(-600, -200, 200)

# ax.add_patch(rect)
plt.title('Comparison with commonly used chilling requirement models')
plt.savefig('export-chillmodels.png')

In [13]:
df[['chilling_hours', 'utah', 'pcu', 'low_chill', 'north_carolina']].to_csv('chill.csv', sep=';')

Multilinear fit with 

In [8]:
def fitFunc(x, k, cu_thr, c, k_cu, k_ins, k_t, k_i_t, k_i_cu, k_t_cu, k_i_t_cu):
    # NB: CR is on the order of 1000s, need to be brought back in line with other params
    chill_sigmoid = 1 / (1 + np.exp(-k * (x[0]/1000 - cu_thr)))
    return c + k_ins * x[1] + k_t * x[2] + k_i_t * x[1] * x[2] + k_cu * chill_sigmoid + k_i_cu * chill_sigmoid * x[1] + k_t_cu * chill_sigmoid * x[2] + k_i_t_cu * chill_sigmoid * x[1] * x[2]

def simplefit(x, c, k_ins, k_t, k_i_t):
    # NB: CR is on the order of 1000s, need to be brought back in line with other params
    return c + k_ins * x[0] + k_t * x[1] + k_i_t * x[0] * x[1]


df_part = df[:datetime(2021, 7, 1)]
x_arr = [df_part['Insolation, kW/m2'], df_part['temp']]

fitParams, fitCovariances = curve_fit(simplefit, x_arr, df_part['Fv/Fm'], [1, 1, 1, 0])
residuals = df_part['Fv/Fm'] - simplefit(x_arr, *fitParams)
ss_res = np.sum(residuals.values ** 2)
ss_tot = np.sum((df_part['Fv/Fm'] - df_part['Fv/Fm'].mean())**2)
print('FvFm', fitParams, f'r^2={1-ss_res/ss_tot:.2f}')
plt.figure()
plt.plot(df_part.index, df_part['Fv/Fm'], label='Measured')
plt.plot(df_part.index, simplefit(x_arr, *fitParams), label='Modeled')
plt.title('Fv/Fm measured vs reconstructed')
plt.legend(('Measured', f'Modeled, r^2={1-ss_res/ss_tot:.2f}'))
plt.ylabel('Fv/Fm')
plt.ylim(-0.05, 1)
plt.xlim(df_part.index[0], df_part.index[-1])
annotate_gt(0, -0.05, 0.05)
plt.savefig('FvFm MLR.png')

fitParams, fitCovariances = curve_fit(simplefit, x_arr, df_part['DIo/RC'], [1, 1, 1, 0])
residuals = df_part['DIo/RC'] - simplefit(x_arr, *fitParams)
ss_res = np.sum(residuals.values ** 2)
ss_tot = np.sum((df_part['DIo/RC'] - df_part['DIo/RC'].mean())**2)
print('DIo/RC', fitParams, f'r^2 = {1-ss_res/ss_tot:.2f}')
plt.figure()
plt.plot(df_part.index, df_part['DIo/RC'], label='Measured')
plt.plot(df_part.index, simplefit(x_arr, *fitParams), label='Modeled')
plt.title('DIo/RC measured vs reconstructed')
plt.legend(('Measured', f'Modeled, r^2={1-ss_res/ss_tot:.2f}'))
plt.ylabel('DIo/RC')
plt.ylim(0, 7000)
plt.xlim(df_part.index[0], df_part.index[-1])
annotate_gt(-600, -200, 300)
plt.savefig('DIoRC MLR.png')

FvFm [ 0.42497963 -0.20569182  0.01959479 -0.004744  ] r^2=0.67
DIo/RC [ 42.44348294 105.94526282  -5.02085177  -1.75549253] r^2 = 0.07
